In [1]:
import math
import torch
import pickle
import torch.cuda
import torchvision.transforms as transforms
import torch.utils.data as data
import torchvision.datasets as dsets
import os
from utils.BBBConvmodel import BBBAlexNet, BBBLeNet, BBB3Conv3FC
from utils.BBBlayers import GaussianVariationalInference
import numpy as np
from scipy.stats import norm, cauchy
cuda = torch.cuda.is_available()
import pandas as pd
from matplotlib import pyplot as plt
import scipy

In [2]:
batch_size = 32
lr = 0.001
dataset = 'CIFAR-10'
network = 'lenet'
epoch = 50
if epoch != 50:
    model = torch.load("../results/{}_b{}_lr{}epoch{}_{}.pth".format(network, batch_size, lr, epoch, dataset))
else:
    model = torch.load("../results/{}_b{}_lr{}_{}.pth".format(network, batch_size, lr, dataset))
net = BBBLeNet
num_samples = 10
beta_type = "Blundell"

In [3]:
# dimensions of input and output
if dataset == 'MNIST':    # train with MNIST
    outputs = 10
    inputs = 1
elif dataset == 'CIFAR-10':  # train with CIFAR-10
    outputs = 10
    inputs = 3
elif dataset == 'CIFAR-100':    # train with CIFAR-100
    outputs = 100
    inputs = 3

if net == BBBLeNet or BBB3Conv3FC:
    resize = 32
elif net == BBBAlexNet:
    resize = 227

In [4]:
'''
LOADING DATASET
'''

if dataset == 'MNIST':
    transform = transforms.Compose([transforms.Resize((resize, resize)), transforms.ToTensor(),
                                    transforms.Normalize((0.1307,), (0.3081,))])
    train_dataset = dsets.MNIST(root="data", download=True, transform=transform)
    val_dataset = dsets.MNIST(root="data", download=True, train=False, transform=transform)

elif dataset == 'CIFAR-100':
    transform = transforms.Compose([transforms.Resize((resize, resize)), transforms.ToTensor(),
                                    transforms.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225))])
    train_dataset = dsets.CIFAR100(root="data", download=True, transform=transform)
    val_dataset = dsets.CIFAR100(root='data', download=True, train=False, transform=transform)

elif dataset == 'CIFAR-10':
    transform = transforms.Compose([transforms.Resize((resize, resize)), transforms.ToTensor(),
                                    transforms.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225))])
    train_dataset = dsets.CIFAR10(root="data", download=True, transform=transform)
    val_dataset = dsets.CIFAR10(root='data', download=True, train=False, transform=transform)

Files already downloaded and verified
Files already downloaded and verified


In [5]:
loader_val = data.DataLoader(dataset=val_dataset, batch_size=batch_size, shuffle=False)

In [6]:
model.state_dict().keys()

odict_keys(['conv1.qw_mean', 'conv1.qw_logvar', 'conv1.qb_mean', 'conv1.qb_logvar', 'conv1.conv_qw_mean', 'conv1.conv_qw_si', 'conv1.log_alpha', 'conv2.qw_mean', 'conv2.qw_logvar', 'conv2.qb_mean', 'conv2.qb_logvar', 'conv2.conv_qw_mean', 'conv2.conv_qw_si', 'conv2.log_alpha', 'fc1.qw_mean', 'fc1.qw_logvar', 'fc1.qb_mean', 'fc1.qb_logvar', 'fc1.fc_qw_mean', 'fc1.fc_qw_si', 'fc1.log_alpha', 'fc2.qw_mean', 'fc2.qw_logvar', 'fc2.qb_mean', 'fc2.qb_logvar', 'fc2.fc_qw_mean', 'fc2.fc_qw_si', 'fc2.log_alpha', 'fc3.qw_mean', 'fc3.qw_logvar', 'fc3.qb_mean', 'fc3.qb_logvar', 'fc3.fc_qw_mean', 'fc3.fc_qw_si', 'fc3.log_alpha', 'layers.0.qw_mean', 'layers.0.qw_logvar', 'layers.0.qb_mean', 'layers.0.qb_logvar', 'layers.0.conv_qw_mean', 'layers.0.conv_qw_si', 'layers.0.log_alpha', 'layers.3.qw_mean', 'layers.3.qw_logvar', 'layers.3.qb_mean', 'layers.3.qb_logvar', 'layers.3.conv_qw_mean', 'layers.3.conv_qw_si', 'layers.3.log_alpha', 'layers.7.qw_mean', 'layers.7.qw_logvar', 'layers.7.qb_mean', 'layers

# 合并weights

In [7]:
w_name = ['layers.0.qw_', 'layers.3.qw_', 'layers.7.qw_','layers.9.qw_', 'layers.11.qw_']
b_name = ['layers.0.qb_', 'layers.3.qb_', 'layers.7.qb_','layers.9.qb_', 'layers.11.qb_']

In [9]:
model = model.cpu()

In [10]:
whole_w = []
for (i, j) in zip(w_name, b_name):
    whole_w.append(model.state_dict()['{}mean'.format(i)].numpy().ravel())
    whole_w.append(model.state_dict()['{}mean'.format(j)].numpy().ravel())
whole_w = np.concatenate(whole_w)

In [11]:
len(whole_w)

62006

In [12]:
len(whole_w[np.abs(whole_w) <= 1e-2])

7562

# 神经网络精度计算函数

In [13]:
vi = GaussianVariationalInference(torch.nn.CrossEntropyLoss())

def run_epoch(loader, epoch, is_training=False):
    m = math.ceil(len(loader.dataset) / loader.batch_size)

    accuracies = []
    likelihoods = []
    kls = []
    losses = []

    for i, (images, labels) in enumerate(loader):
        # # Repeat samples (Casper's trick)
        # x = images.view(-1, inputs, resize, resize).repeat(num_samples, 1, 1, 1)
        # y = labels.repeat(num_samples)
        x = images.view(-1, inputs, resize, resize)
        y = labels
        if cuda:
            x = x.cuda()
            y = y.cuda()

        if beta_type == "Blundell":
            beta = 2 ** (m - (i + 1)) / (2 ** m - 1)
        elif beta_type == "Soenderby":
            beta = min(epoch / (num_epochs//4), 1)
        elif beta_type == "Standard":
            beta = 1 / m
        else:
            beta = 0

        logits, kl = model.probforward(x)
        loss = vi(logits, y, kl, beta)
        ll = -loss.data.mean() + beta*kl.data.mean()

        if is_training:
            optimiser.zero_grad()
            loss.backward()
            optimiser.step()

        _, predicted = logits.max(1)
        accuracy = (predicted.data.cpu() == y.cpu()).float().mean()

        accuracies.append(accuracy)
        losses.append(loss.data.mean())
        kls.append(beta*kl.data.mean())
        likelihoods.append(ll)

    diagnostics = {'loss': sum(losses)/len(losses),
                   'acc': sum(accuracies)/len(accuracies),
                   'kl': sum(kls)/len(kls),
                   'likelihood': sum(likelihoods)/len(likelihoods)}

    return diagnostics

In [14]:
model = model.cuda()
diagnostics_val = run_epoch(loader_val, epoch=1)

logits tensor([[-2.0574, -3.5037,  0.0478,  3.4333, -2.0460,  3.1696,  0.7671, -0.4434,
          0.3641, -3.1879],
        [ 4.3210,  4.1046, -2.4593, -4.8865, -4.2505, -5.4343, -5.8693, -5.2282,
          7.5127,  1.3391],
        [ 2.0754,  1.7715, -1.5878, -1.8178, -3.0975, -2.3988, -4.2723, -2.0059,
          3.3131,  1.2492],
        [ 4.7542, -0.0598,  2.2648, -1.6019, -2.1577, -3.5182, -3.3867, -5.6720,
          4.2865, -1.4069],
        [-4.0529, -3.3052,  1.1162,  1.8004,  4.0378,  1.3750,  2.3166, -0.7092,
         -4.5464, -3.5764],
        [-1.4519, -4.1841,  1.2928,  1.0634,  0.2107,  1.2363,  3.2781,  0.2540,
         -4.9777, -3.1666],
        [ 1.5608,  2.5139,  0.7801,  0.3607, -3.8347,  0.3170, -1.5263, -1.7832,
         -4.0454, -0.2909],
        [-2.1739, -2.3404,  1.6988, -0.0506,  1.3337, -1.1882,  3.3673, -1.5012,
         -2.8533, -1.5919],
        [-0.3826, -4.0845,  2.0298,  2.6623,  0.8054,  2.6306, -0.4322,  1.3401,
         -3.8687, -3.3382],
        [-0.

In [15]:
def evaluate(loader, epoch=1):
    m = math.ceil(len(loader.dataset) / loader.batch_size)

    accuracies = []

    for i, (images, labels) in enumerate(loader):
        # # Repeat samples (Casper's trick)
        # x = images.view(-1, inputs, resize, resize).repeat(num_samples, 1, 1, 1)
        # y = labels.repeat(num_samples)

        x = images.view(-1, inputs, resize, resize)
        y = labels

        if cuda:
            x = x.cuda()
            y = y.cuda()

        logits = cpr_model(x)
        _, predicted = torch.max(logits.data, 1)
        accuracy = (predicted.data.cpu() == y.cpu()).float().mean()

        accuracies.append(accuracy)

    diagnostics = {'acc': sum(accuracies)/len(accuracies)}

    return diagnostics

# all layers放在一起压缩

In [16]:
def compress_coordinates(means, stds, beta, bitlengths):
    # N = len(means.ravel()) = len(stds.ravel())
    # C = len(codepoints)
    optima = np.empty_like(means)
    optima_lengths = np.empty_like(means, dtype=int)
    for i in range(0, 10000000, 100000):
        if i % 100000 == 0:
            print(i / 1000000)
        squared_errors = (codepoints[np.newaxis, :] - means.ravel()[i:i+100000, np.newaxis])**2
            # shape (N, C)
        weighted_penalties = (2 * beta) * stds.ravel()[i:i+100000, np.newaxis]**2 * bitlengths[np.newaxis, :]
            # shape (N, C)
        optima_idxs = np.argmin(squared_errors + weighted_penalties, axis=1)
        optima.ravel()[i:i+100000] = codepoints[optima_idxs]
        optima_lengths.ravel()[i:i+100000] = bitlengths[optima_idxs]
    return optima, optima_lengths

In [17]:
model = model.cpu()

In [19]:
results = [['full', 'full', diagnostics_val['acc'].numpy(), 'None']]
compressed_len_list = []
betas = [0.0001, 0.001, 0.01, 0.1, 1, 10, 100]
bitlengths = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
# betas = [0.01]
# bitlengths = [2]

cauchy_loc, cauchy_scale = cauchy.fit(whole_w)

for max_codepoint_length in bitlengths:
    for beta_ in betas:
        compressed_len = 0
        compressed_list = []
        for (i, j) in zip(w_name, b_name):
            codepoints_and_lengths = [
                (scipy.stats.cauchy.ppf(codepoint_xi, loc=cauchy_loc, scale=cauchy_scale), length)
                for length in range(max_codepoint_length+1)
                for codepoint_xi in np.arange(0.5**(length+1), 1, 0.5**length)
            ]
            codepoints = np.array([codepoint for codepoint, _ in codepoints_and_lengths])
            lengths = np.array([length for _, length in codepoints_and_lengths])
            # compress w
            vecs_u1 = model.state_dict()['{}mean'.format(i)].numpy()
            stds_u1 = np.exp(model.state_dict()['{}logvar'.format(i)].numpy())
            compressed1, cpr_len1 = compress_coordinates(vecs_u1,stds_u1,beta_,lengths)
            compressed1 = torch.from_numpy(compressed1)
            compressed_list.append(compressed1)
            compressed_len += np.sum(cpr_len1)
            # compress b
            vecs_u2 = model.state_dict()['{}mean'.format(j)].numpy()
            stds_u2 = np.exp(model.state_dict()['{}logvar'.format(j)].numpy())
            compressed2, cpr_len2 = compress_coordinates(vecs_u2,stds_u2,beta_,lengths)
            compressed2 = torch.from_numpy(compressed2)
            compressed_list.append(compressed2)
            compressed_len += np.sum(cpr_len2)

        compressed_len_list.append([max_codepoint_length, beta_, compressed_len, 'global'])
        
        # lenet
        from model import lenet
        cpr_model=lenet(inputs)
        print(max_codepoint_length, beta_)
        name_cpr=cpr_model.state_dict().keys()
        cpr_state_dict = dict(zip(name_cpr, compressed_list))
        cpr_model.load_state_dict(cpr_state_dict)
        # 用压缩后的模型计算loss，acc等
        cpr_model = cpr_model.cuda()
        diagnostics_cpr_val = evaluate(loader_val)
        results.append([max_codepoint_length, beta_, diagnostics_cpr_val['acc'].numpy(), 'global'])

0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9


# 每层用不同P(z)

In [18]:
for max_codepoint_length in bitlengths:
    for beta_ in betas:
        compressed_len = 0
        compressed_list = []
        for (i, j) in zip(w_name, b_name):
            # w
            vecs_u1 = model.state_dict()['{}mean'.format(i)].numpy()
            stds_u1 = np.exp(model.state_dict()['{}logvar'.format(i)].numpy())
            # b
            vecs_u2 = model.state_dict()['{}mean'.format(j)].numpy()
            stds_u2 = np.exp(model.state_dict()['{}logvar'.format(j)].numpy())
            # 先把w和b合并在一起再拟合高斯
            vecs_u = np.concatenate([vecs_u1.ravel(), vecs_u2.ravel()])

            cauchy_loc, cauchy_scale = cauchy.fit(vecs_u.ravel())
            codepoints_and_lengths = [
                (scipy.stats.cauchy.ppf(codepoint_xi, loc=cauchy_loc, scale=cauchy_scale), length)
                for length in range(max_codepoint_length+1)
                for codepoint_xi in np.arange(0.5**(length+1), 1, 0.5**length)
            ]
            codepoints = np.array([codepoint for codepoint, _ in codepoints_and_lengths])
            lengths = np.array([length for _, length in codepoints_and_lengths])

            compressed1, cpr_len1 = compress_coordinates(vecs_u1,stds_u1,beta_,lengths)
            compressed1 = torch.from_numpy(compressed1)
            compressed_list.append(compressed1)
            compressed_len += np.sum(cpr_len1)
            # compress b
            compressed2, cpr_len2 = compress_coordinates(vecs_u2,stds_u2,beta_,lengths)
            compressed2 = torch.from_numpy(compressed2)
            compressed_list.append(compressed2)
            compressed_len += np.sum(cpr_len2)

        compressed_len_list.append([max_codepoint_length, beta_, compressed_len, 'layer-wise'])
        # lenet
        from bayesian.codes.model import lenet_b
        cpr_model=lenet_b(inputs)
        print(max_codepoint_length, beta_)
        print(compressed_list)
        name_cpr=cpr_model.state_dict().keys()
        cpr_state_dict = dict(zip(name_cpr, compressed_list))
        cpr_model.load_state_dict(cpr_state_dict)
        cpr_model = cpr_model.cuda()
        # 用压缩后的模型计算loss，acc等
        diagnostics_cpr_val = evaluate(loader_val)
        results.append([max_codepoint_length, beta_, diagnostics_cpr_val['acc'].numpy(), 'layer-wise'])

0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9


In [19]:
results = pd.DataFrame(results)
results.columns = ['bitlength', 'beta', 'acc_test', 'method']

In [20]:
results

[['full', 'full', array(0.6009385, dtype=float32), 'None'],
 [1, 0.0001, array(0.11491613, dtype=float32), 'global'],
 [1, 0.001, array(0.11281949, dtype=float32), 'global'],
 [1, 0.01, array(0.11331869, dtype=float32), 'global'],
 [1, 0.1, array(0.09984025, dtype=float32), 'global'],
 [1, 1, array(0.10013977, dtype=float32), 'global'],
 [1, 10, array(0.10013977, dtype=float32), 'global'],
 [1, 100, array(0.09984025, dtype=float32), 'global'],
 [2, 0.0001, array(0.31988817, dtype=float32), 'global'],
 [2, 0.001, array(0.32827476, dtype=float32), 'global'],
 [2, 0.01, array(0.27595848, dtype=float32), 'global'],
 [2, 0.1, array(0.09984025, dtype=float32), 'global'],
 [2, 1, array(0.10013977, dtype=float32), 'global'],
 [2, 10, array(0.10013977, dtype=float32), 'global'],
 [2, 100, array(0.09984025, dtype=float32), 'global'],
 [3, 0.0001, array(0.3613219, dtype=float32), 'global'],
 [3, 0.001, array(0.35732827, dtype=float32), 'global'],
 [3, 0.01, array(0.33516374, dtype=float32), 'glob

In [20]:
results.to_csv("./results/lenet_withbias_b{}_lr{}_{}_cauchy.csv".format(batch_size, lr, dataset), index=False)

In [21]:
cpr_len_df = pd.DataFrame(compressed_len_list)
cpr_len_df.columns = ['bitlength', 'beta', 'len', 'method']
cpr_len_df['len'] = cpr_len_df['len'] / whole_w.size

In [22]:
cpr_len_df

bitlength      beta       len      method
0            1    0.0001  0.719269      global
1            1    0.0010  0.719269      global
2            1    0.0100  0.719140      global
3            1    0.1000  0.718656      global
4            1    1.0000  0.713125      global
..         ...       ...       ...         ...
135         10    0.0100  5.459391  layer-wise
136         10    0.1000  3.863029  layer-wise
137         10    1.0000  2.414944  layer-wise
138         10   10.0000  1.300890  layer-wise
139         10  100.0000  0.531320  layer-wise

[140 rows x 4 columns]

In [23]:
cpr_len_df.to_csv("./results/bits_lenet_withbias_b{}_lr{}_{}_cauchy.csv".format(batch_size, lr, dataset), index=False)